In [ ]:
!pip install -q datasets transformers[sentencepiece] simpletransformers
!pip install -q scikit-learn

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.4/42.4 kB 2.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.6/43.6 kB 4.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.3/44.3 kB 3.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 480.6/480.6 kB 22.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 316.3/316.3 kB 29.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 179.3/179.3 kB 13.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.1/9.1 MB 94.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 101.7/101.7 kB 10.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.8/194.8 kB 19.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.9/6.9 MB 82.1 MB/s eta 0:00:0

In [ ]:
!unzip /content/super-ai-ss-5-named-entity-recognition.zip -d /content/super-ai-ss-5-named-entity-recognition > /dev/null

In [ ]:
!mv /content/super-ai-ss-5-named-entity-recognition/train/train/* /content/super-ai-ss-5-named-entity-recognition/train
!rm -rf /content/super-ai-ss-5-named-entity-recognition/train/train
!mv /content/super-ai-ss-5-named-entity-recognition/eval/eval/* /content/super-ai-ss-5-named-entity-recognition/eval
!rm -rf /content/super-ai-ss-5-named-entity-recognition/eval/eval
!mv /content/super-ai-ss-5-named-entity-recognition/test/test/* /content/super-ai-ss-5-named-entity-recognition/test
!rm -rf /content/super-ai-ss-5-named-entity-recognition/test/test

In [ ]:
import pandas as pd
from datasets import load_dataset
from simpletransformers.ner import NERModel, NERArgs
import scipy as sp

In [ ]:
# load dataset from folder 'data' with three folders 'train', 'test', 'eval' containing txt files containing JOHN	VV	O	B_CLS
dataset = load_dataset("customds.py", data_dir="super-ai-ss-5-named-entity-recognition", trust_remote_code=True)

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

In [ ]:
dataset

DatasetDict({
    train: Dataset({
        features: ['id', 'fname', 'tokens', 'pos_tags', 'ner_tags', 'clause_tags'],
        num_rows: 63310
    })
    validation: Dataset({
        features: ['id', 'fname', 'tokens', 'pos_tags', 'ner_tags', 'clause_tags'],
        num_rows: 5620
    })
    test: Dataset({
        features: ['id', 'fname', 'tokens', 'pos_tags', 'ner_tags', 'clause_tags'],
        num_rows: 5242
    })
})

In [ ]:
train_df = pd.DataFrame(dataset['train'])
eval_df = pd.DataFrame(dataset['validation'])

In [ ]:
# add half of eval data to train data
train_df = pd.concat([train_df, eval_df[:int(len(eval_df)/2)]]).reset_index(drop=True)
eval_df = eval_df[int(len(eval_df)/2):].reset_index(drop=True)

In [ ]:
train_df["token_length"] = train_df["tokens"].apply(len)
train_df["ner_tags_length"] = train_df["ner_tags"].apply(len)
# trim any tokens that are too long to 128
train_df["tokens"] = train_df["tokens"].apply(lambda x: x[:128])
train_df["ner_tags"] = train_df["ner_tags"].apply(lambda x: x[:128])
train_df["clause_tags"] = train_df["clause_tags"].apply(lambda x: x[:128])

eval_df["tokens"] = eval_df["tokens"].apply(lambda x: x[:128])
eval_df["ner_tags"] = eval_df["ner_tags"].apply(lambda x: x[:128])
eval_df["clause_tags"] = eval_df["clause_tags"].apply(lambda x: x[:128])


In [ ]:
test=pd.DataFrame(dataset["test"])

In [ ]:
test.head(50)

id      fname                                             tokens  \
0    0  03795.txt  [รัฐ, ถังแตก, วิก, _, 7, _, สี, ชวด, โบนัส, ธน...   
1    1  03795.txt  [นาย, แอนศิริ, _, วลัยกนก, _, ผู้, รัฐมนตรี, _...   
2    2  03795.txt  [แต่, ประเด็น, คือ, _, ยัง, ไม่, มี, ใคร, รู้,...   
3    3  03795.txt  [แหล่ง, ข่าว, จากที่, ประชุม, _, พลังงานแห่งชา...   
4    4  03795.txt  [และ, _, ขอ, จัดสรร, เงิน, สมทบ, จาก, งบ, กลาง...   
5    5  03795.txt  [แต่, _, นายก, รัฐมนตรี, ขอ, ให้, ถอน, เรื่อง,...   
6    6  03795.txt  [โดย, อาจ, ต้อง, ปรับปรุง, หลักเกณฑ์, การ, จัด...   
7    7  03795.txt  [แหล่ง, ข่าว, กล่าว, ว่า, _, เรื่อง, ดังกล่าว,...   
8    8  03795.txt  [การ, ปรับ, เงิน, ค่า, ตอบแทน, บุคลากร, ภาค, ร...   
9    9  03795.txt  [ทั้งนี้, ที่, ประชุม, _, สน.บางกอกน้อย, _, เห...   
10  10  03795.txt  [ใน, มาตรา, _, 48, _, และ, _, 49, _, ใน, _, พ....   
11  11  03795.txt  [และ, ให้, _, มิตซูบิชิ, เสนอ, _, ขบวนการ, มูจ...   
12  12  03795.txt  [แต่, ปี, นี้, _, กองทัพ, ภาค, ที่, _, 1, เสนอ...   
13  13  03795.txt  [รายงาน, ข่าว, แจ้ง, ว่า, _, ก่อนหน้า, นั้น, น...   
14  14  03795.txt  [ส่วน, ปี, งบประมาณ, _, 2554, _, จะ, มี, หรือไ...   
15   0  03796.txt  [FIA, ยัน, หน., กบฏพยัคฆ์ทมิฬอีแลม, ถูก, จับ, ...   
16   1  03796.txt  [เมื่อ, เวลา, _, 12.00, _, น., _, วัน, นี้, (,...   
17   2  03796.txt  [ขณะ, เดียว, กัน, _, เว็บไซต์, ของ, กลุ่ม, ดัง...   
18   3  03796.txt  [ตอน, นี้, ทางการ, ตลาด, มหาชัย, ยัง, ไม่, มี,...   
19   4  03796.txt  [อย่างไรก็ตาม, _, มี, ข้อมูล, ที่, ระบุ, ว่า, ...   
20   0  03797.txt  [กกต., กลาง, _, เลื่อน, อ่าน, คำ, พิพากษา, คดี...   
21   1  03797.txt  [อสมท, _, มี, คำสั่ง, ให้, เลื่อน, การ, อ่าน, ...   
22   2  03797.txt  [องค์, คณะ, ผู้, พิพากษา, คณะ, กรรมการ, บริหาร...   
23   3  03797.txt  [นาย, นุชนาถ, _, โกฏคำลือ, _, อดีต, ฤาษี, นายก...   
24   4  03797.txt  [นาย, ปรีดา, _, สวัสดิผล, _, อดีต, _, รัฐมนตรี...   
25   5  03797.txt  [นาย, สันต์, _, เจริญศิลป์, _, อดีต, _, รัฐมนต...   
26   6  03797.txt  [นาย, พีระเดช, _, เลาหะโรจนพันธ์, _, อดีต, สบ,...   
27   7  03797.txt  [และ, นาย, อรรถพล, _, เดชเดโช, _, อดีต, _, รัฐ...   
28   8  03797.txt  [กลุ่ม, คณะ, กรรมการ, บริหาร, โครงการ, กำหนด, ...   
29   9  03797.txt  [ใน, ความ, ผิด, ฐาน, เป็น, เจ้าพนักงาน, มี, หน...   
30  10  03797.txt  [พ.ร.บ., ว่า, ด้วย, ความ, ผิด, เกี่ยวกับ, การ,...   
31  11  03797.txt  [แต่, นาย, อนุชา, _, ไม่, เดินทาง, มา, ศาล, _,...   
32  12  03797.txt  [ศาล, พิเคราะห์, แล้ว, เห็น, ว่า, _, นาย, ชัยท...   
33  13  03797.txt  [หาก, จำเลย, จะ, ไป, รักษา, ตัว, ยัง, ต่าง, ปร...   
34  14  03797.txt  [พร้อม, ให้, ปรับ, _, นายประกัน, _, เป็น, เงิน...   
35  15  03797.txt  [โดย, กำหนด, ให้, ชำระ, ค่า, ประกัน, ภายใน, _,...   
36  16  03797.txt  [อย่างไรก็ตาม, ศาล, ฯ, ได้, กำชับ, จำเลย, ทั้ง...   
37   0  03798.txt  [ไข้, หวัด, _, 2009, _, พ่นพิษ, _, SMEs, _, สอ...   
38   1  03798.txt  [ไข้, หวัด, ใหญ่, สาย, พันธุ์, ใหม่, _, 2009, ...   
39   2  03798.txt  [ขณะ, ที่, ยอด, ส่ง, ออก, _, 6, _, เดือน, แรก,...   
40   3  03798.txt  [ดร., สรรพภัญญู, _, บัวบาน, _, ผู้, อำนวยการ, ...   
41   4  03798.txt  [ที่, คาดการณ์, ไว้, ว่า, ตลอด, ทั้ง, ปี, จะ, ...   
42   5  03798.txt  [ทั้งนี้, _, สาขา, ธุรกิจ, ที่, จะ, ได้รับ, ผล...   
43   6  03798.txt  [นอกจาก, นั้น, _, ผล, กระทบ, ที่, เกิด, ขึ้น, ...   
44   7  03798.txt  [เนื่องจาก, เอสเอ็มอี, มี, ข้อ, จำกัด, ใน, หลา...   
45   8  03798.txt  [ดังนั้น, _, เมื่อ, เกิด, วิกฤต, เศรษฐกิจ, _, ...   
46   9  03798.txt  [ดร., ธิษะณา, _, ระบุ, ด้วย, ว่า, _, สิ่ง, สำค...   
47  10  03798.txt  [ทั้งนี้, _, ใน, ส่วน, ของ, สถานการณ์, ส่ง, ออ...   
48  11  03798.txt  [ไตรมาส, ที่, _, 1, _, ยอด, ส่ง, ออก, รวม, มี,...   
49  12  03798.txt  [ส่วน, ไตรมาส, _, 2, _, ยอด, ส่ง, ออก, ลด, ลง,...   

                                             pos_tags  \
0   [0, 1, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, ...   
1   [0, 0, 2, 0, 2, 0, 0, 2, 1, 3, 3, 0, 0, 2, 2, ...   
2   [3, 0, 1, 2, 5, 12, 1, 11, 1, 3, 1, 0, 1, 1, 6...   
3   [0, 0, 3, 0, 2, 0, 2, 1, 3, 2, 0, 0, 0, 0, 2, ...   
4   [3, 2, 1, 1, 0, 1, 4, 0, 0, 0, 2, 8, 2, 3,

In [ ]:
_POS_TAGS = ["NN", "VV", "PU", "CC", "PS", "AX", "AV", "FX", "NU", "AJ", "CL", "PR", "NG", "PA", "XX", "IJ"]
_NER_TAGS = [
        "O",
        "B_BRN",
        "B_DES",
        "B_DTM",
        "B_LOC",
        "B_MEA",
        "B_NUM",
        "B_ORG",
        "B_PER",
        "B_TRM",
        "B_TTL",
        "I_BRN",
        "I_DES",
        "I_DTM",
        "I_LOC",
        "I_MEA",
        "I_NUM",
        "I_ORG",
        "I_PER",
        "I_TRM",
        "I_TTL",
        "E_BRN",
        "E_DES",
        "E_DTM",
        "E_LOC",
        "E_MEA",
        "E_NUM",
        "E_ORG",
        "E_PER",
        "E_TRM",
        "E_TTL",
    ]
_CLAUSE_TAGS = ["O", "B_CLS", "I_CLS", "E_CLS"]

In [ ]:
train_df["tokens"][0]

['สภาสังคมสงเคราะห์แห่งประเทศ',
 'ไทย',
 'จี้',
 'ศาล',
 'ไฟเขียว',
 'ขาย',
 'สินทรัพย์',
 'ปู',
 'ทาง',
 'ปรับ',
 'โครงสร้าง']

In [ ]:
print(list(train_df["tokens"][0]))
print(list(train_df["ner_tags"][0]))
print(list(map(lambda x: _NER_TAGS[x], train_df["ner_tags"][0])))

['สภาสังคมสงเคราะห์แห่งประเทศ', 'ไทย', 'จี้', 'ศาล', 'ไฟเขียว', 'ขาย', 'สินทรัพย์', 'ปู', 'ทาง', 'ปรับ', 'โครงสร้าง']
[7, 27, 0, 0, 0, 0, 0, 0, 0, 0, 0]
['B_ORG', 'E_ORG', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O']


In [ ]:
def convert_to_simple_transformer_format(df, field_name, tags):
  sentence_id = []
  words = []
  labels = []

  for (idx, r) in df.iterrows():
    for (i, t) in enumerate(r['tokens']):
      sentence_id.append(idx)
      words.append(t)
      labels.append(tags[r[field_name][i]])

  return pd.DataFrame(
      {"sentence_id": sentence_id, "words": words, "labels": labels}
  )

In [ ]:
train_ = convert_to_simple_transformer_format(train_df, "ner_tags", _NER_TAGS)
validation_ = convert_to_simple_transformer_format(eval_df, "ner_tags", _NER_TAGS)
test_ = convert_to_simple_transformer_format(test, "ner_tags", _NER_TAGS)

In [ ]:
ner_args = NERArgs()
ner_args.train_batch_size = 256
ner_args.use_multiprocessing = True
ner_args.evaluate_during_training = True
ner_args.overwrite_output_dir = True
ner_args.eval_batch_size = 64
ner_args.num_train_epochs = 20
ner_args.gradient_accumulation_steps = 4
ner_args.learning_rate = 5e-5
ner_args.max_seq_length	= 128

In [ ]:
model = NERModel(
    "camembert",
    "airesearch/wangchanberta-base-att-spm-uncased",
    args=ner_args,
    use_cuda=True,
    labels=_NER_TAGS
)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/546 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/423M [00:00<?, ?B/s]

Some weights of CamembertForTokenClassification were not initialized from the model checkpoint at airesearch/wangchanberta-base-att-spm-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


tokenizer_config.json:   0%|          | 0.00/282 [00:00<?, ?B/s]

sentencepiece.bpe.model:   0%|          | 0.00/905k [00:00<?, ?B/s]

/usr/local/lib/python3.11/dist-packages/simpletransformers/ner/ner_model.py:433: UserWarning: use_multiprocessing automatically disabled as CamemBERT fails when using multiprocessing for feature conversion.
  warnings.warn(


In [ ]:
model.train_model(train_, eval_data=validation_)

  0%|          | 0/66120 [00:00<?, ?it/s]

Epoch:   0%|          | 0/20 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/simpletransformers/ner/ner_model.py:758: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = amp.GradScaler()


Running Epoch 1 of 20:   0%|          | 0/259 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/simpletransformers/ner/ner_model.py:782: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


...

Running Evaluation:   0%|          | 0/44 [00:00<?, ?it/s]

Running Epoch 20 of 20:   0%|          | 0/259 [00:00<?, ?it/s]

  0%|          | 0/2 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/44 [00:00<?, ?it/s]

(1280,
 defaultdict(list,
             {'global_step': [64,
               128,
               192,
               256,
               320,
               384,
               448,
               512,
               576,
               640,
               704,
               768,
               832,
               896,
               960,
               1024,
               1088,
               1152,
               1216,
               1280],
              'train_loss': [0.4651058316230774,
               0.14381475746631622,
               0.13946391642093658,
               0.08236152678728104,
               0.06251239031553268,
               0.06609057635068893,
               0.050188466906547546,
               0.06306164711713791,
               0.045061130076646805,
               0.048799753189086914,
               0.040800414979457855,
               0.05404221639037132,
               0.04015326499938965,
               0.032761361449956894,
               0.048186503350734

In [ ]:
ner_args = NERArgs()
ner_args.eval_batch_size = 256
ner_args.max_seq_length = 512
ner_args.use_multiprocessing = True
model = NERModel("auto",
    '/content/outputs/best_model',
    args=ner_args,
    use_cuda=True,
    labels= _NER_TAGS
)

In [ ]:
test_set = []
for i in range(len(test)):
    test_set.append(list(test["tokens"][i]))

In [ ]:
# count elements in test_set
count = 0
for i in range(len(test_set)):
    count += len(test_set[i])
print(count)

213091


In [ ]:
predictions, raw_outputs = model.predict(test_set, False)

  0%|          | 0/2 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/21 [00:00<?, ?it/s]

/usr/local/lib/python3.11/dist-packages/simpletransformers/ner/ner_model.py:1643: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with amp.autocast():


In [ ]:
predictions_, raw_outputs_ = model.predict([test_set[5][:]], False)

  0%|          | 0/1 [00:00<?, ?it/s]

Running Prediction:   0%|          | 0/1 [00:00<?, ?it/s]

In [ ]:
predictions_

[[{'แต่': 'E_TTL'},
  {'_': 'B_LOC'},
  {'นายก': 'E_MEA'},
  {'รัฐมนตรี': 'B_DES'},
  {'ขอ': 'E_MEA'},
  {'ให้': 'B_DES'},
  {'ถอน': 'B_LOC'},
  {'เรื่อง': 'I_DTM'},
  {'ไป': 'B_LOC'},
  {'ก่อน': 'B_DES'},
  {'_': 'B_LOC'},
  {'เพื่อ': 'O'},
  {'ไป': 'B_LOC'},
  {'ดู': 'I_DTM'},
  {'ประมาณ': 'B_LOC'},
  {'การ': 'B_LOC'},
  {'ตัว': 'B_LOC'},
  {'เลข': 'B_LOC'},
  {'งบประมาณ': 'B_DES'},
  {'จาก': 'B_DES'},
  {'ปี': 'B_DES'},
  {'ก่อน': 'B_DES'},
  {'_': 'B_LOC'},
  {'และ': 'I_DTM'},
  {'ข้อมูล': 'B_LOC'},
  {'จาก': 'B_LOC'},
  {'กรมบัญชีกลาง': 'B_DES'},
  {'ว่า': 'B_LOC'},
  {'_': 'I_ORG'},
  {'จะ': 'O'},
  {'มี': 'I_ORG'},
  {'เงิน': 'B_DES'},
  {'เหลือ': 'I_ORG'},
  {'จ่าย': 'B_LOC'},
  {'เพียงพอ': 'B_LOC'},
  {'หรือไม่': 'B_LOC'},
  {'_': 'B_LOC'},
  {'โดย': 'I_DTM'},
  {'ให้': 'B_LOC'},
  {'_': 'B_LOC'},
  {'กรม': 'I_BRN'},
  {'_': 'B_DES'},
  {'ไป': 'B_BRN'},
  {'ทำ': 'E_TTL'},
  {'ความ': 'B_LOC'},
  {'ตกลง': 'B_TTL'},
  {'กับ': 'B_LOC'},
  {'กรมบัญชีกลาง': 'B_DES'},
  {'_': 'B_LOC'

In [ ]:
len(test_set)

5242

In [ ]:
len(predictions)

5242

In [ ]:
# find length mismatch between test_set and predictions
for i in range(len(test_set)):
    if len(test_set[i]) != len(predictions[i]):
        print(i)
        print(len(test_set[i]))
        print(len(predictions[i]))
        # find what went missing
        # for j in range(len(test_set[i])):
        #     if test_set[i][j] not in predictions[i]:
        #         print(test_set[i][j])
        # break

In [ ]:
i = 5
print(test_set[i])
print("------")
print(predictions[i])

['แต่', '_', 'นายก', 'รัฐมนตรี', 'ขอ', 'ให้', 'ถอน', 'เรื่อง', 'ไป', 'ก่อน', '_', 'เพื่อ', 'ไป', 'ดู', 'ประมาณ', 'การ', 'ตัว', 'เลข', 'งบประมาณ', 'จาก', 'ปี', 'ก่อน', '_', 'และ', 'ข้อมูล', 'จาก', 'กรมบัญชีกลาง', 'ว่า', '_', 'จะ', 'มี', 'เงิน', 'เหลือ', 'จ่าย', 'เพียงพอ', 'หรือไม่', '_', 'โดย', 'ให้', '_', 'กรม', '_', 'ไป', 'ทำ', 'ความ', 'ตกลง', 'กับ', 'กรมบัญชีกลาง', '_', 'เพื่อ', 'เสนอ', 'แก้ไข', 'ระเบียบ', 'ของ', 'กรมบัญชี', '_', 'ที่', 'กำหนด', 'ให้', 'นำ', 'เงิน', 'เหลือ', 'จ่าย', 'มา', 'ใช้', 'ได้', 'ไม่', 'เกิน', '_', '50', '_', '%', '_', 'มา', 'ให้', 'เพื่อ', 'การ', 'พัฒนา', 'องค์กร', '_', 'เพื่อ', 'ให้', 'นำ', 'ไป', 'ใช้', 'จัดสรร', 'เป็น', 'เงิน', 'รางวัล', 'ประจำ', 'ปี']
------
[{'แต่': 'O'}, {'_': 'O'}, {'นายก': 'O'}, {'รัฐมนตรี': 'O'}, {'ขอ': 'O'}, {'ให้': 'O'}, {'ถอน': 'O'}, {'เรื่อง': 'O'}, {'ไป': 'O'}, {'ก่อน': 'O'}, {'_': 'O'}, {'เพื่อ': 'O'}, {'ไป': 'O'}, {'ดู': 'O'}, {'ประมาณ': 'O'}, {'การ': 'O'}, {'ตัว': 'O'}, {'เลข': 'O'}, {'งบประมาณ': 'O'}, {'จาก': 'O'}, {'ปี': 'O'

In [ ]:
predictions

[[{'รัฐ': 'O'},
  {'ถังแตก': 'O'},
  {'วิก': 'B_ORG'},
  {'_': 'I_ORG'},
  {'7': 'I_ORG'},
  {'_': 'I_ORG'},
  {'สี': 'E_ORG'},
  {'ชวด': 'O'},
  {'โบนัส': 'O'},
  {'ธนาคาร': 'B_ORG'},
  {'นครหลวงไทย': 'I_ORG'},
  {'_': 'I_ORG'},
  {'สาขา': 'I_ORG'},
  {'สยามสแควร์': 'E_ORG'},
  {'ดัน': 'O'},
  {'เข้า': 'O'},
  {'สพช.': 'B_ORG'},
  {'แต่': 'O'},
  {'ถูก': 'O'},
  {'เบรก': 'O'}],
 [{'นาย': 'B_TTL'},
  {'แอนศิริ': 'B_PER'},
  {'_': 'I_PER'},
  {'วลัยกนก': 'E_PER'},
  {'_': 'O'},
  {'ผู้': 'O'},
  {'รัฐมนตรี': 'O'},
  {'_': 'O'},
  {'กล่าว': 'O'},
  {'ว่า': 'O'},
  {'จากที่': 'O'},
  {'ขบวนการ': 'B_ORG'},
  {'มูจาฮีดีน': 'E_ORG'},
  {'_': 'O'},
  {'(': 'O'},
  {'ค่ายจุฬาภรณ์': 'B_ORG'},
  {')': 'O'},
  {'_': 'O'},
  {'เสนอ': 'O'},
  {'ให้': 'O'},
  {'โบนัส': 'O'},
  {'ข้าราชการ': 'O'},
  {'ประจำ': 'O'},
  {'ปี': 'B_DTM'},
  {'_': 'I_DTM'},
  {'2552': 'E_DTM'},
  {'_': 'O'},
  {'จำนวน': 'O'},
  {'_': 'O'},
  {'6': 'B_MEA'},
  {'_': 'I_MEA'},
  {'พัน': 'I_MEA'},
  {'กว่า': 'I_MEA'},
  {'ล้า

In [ ]:
test_tag = pd.read_csv("super-ai-ss-5-named-entity-recognition/tag_list.csv")
tag2class = {}
for i in range(len(test_tag)):
  tag2class[test_tag.loc[i, "tag"]] = test_tag.loc[i, "class"] #Extract data value from dict list
final_test_df = []
for i in range(len(predictions)):
  for j in range(len(predictions[i])):
    data = predictions[i][j]
    value = data.values()
    final_test_df += value

In [ ]:
len(final_test_df)

202204

In [ ]:
# write final_test_df to json
import json
with open('final_test_df.json', 'w') as f:
    json.dump(final_test_df, f)

In [ ]:
# write predictions to json
import json
with open('predictions.json', 'w', encoding='utf-8') as f:
    json.dump(predictions, f, ensure_ascii=False)

In [ ]:
final_test_df[2]

'B_ORG'

In [ ]:
# zip /content/outputs/best_model
!zip -r /content/best_model_ner1.zip /content/outputs/best_model

  adding: content/outputs/best_model/ (stored 0%)
  adding: content/outputs/best_model/config.json (deflated 61%)
  adding: content/outputs/best_model/scheduler.pt (deflated 55%)
  adding: content/outputs/best_model/sentencepiece.bpe.model (deflated 57%)
  adding: content/outputs/best_model/eval_results.txt (deflated 22%)
  adding: content/outputs/best_model/optimizer.pt (deflated 17%)
  adding: content/outputs/best_model/training_args.bin (deflated 51%)
  adding: content/outputs/best_model/model.safetensors (deflated 7%)
  adding: content/outputs/best_model/model_args.json (deflated 61%)
  adding: content/outputs/best_model/special_tokens_map.json (deflated 51%)
  adding: content/outputs/best_model/tokenizer_config.json (deflated 82%)


In [ ]:
test_tag = pd.read_csv("super-ai-ss-5-named-entity-recognition/tag_list.csv")
tag2class = {}
for i in range(len(test_tag)):
  tag2class[test_tag.loc[i, "tag"]] = test_tag.loc[i, "class"] #Extract data value from dict list
final_test_df = []
for i in range(len(predictions)):
  for j in range(len(predictions[i])):
    data = predictions[i][j]
    value = data.values()
    final_test_df += value
  # fill the missing value with "O"
  for k in range(len(test_set[i]) - len(predictions[i])):
    final_test_df += "O"

In [ ]:
print(final_test_df)
# map tag to class
for i in range(len(final_test_df)):
  final_test_df[i] = tag2class[final_test_df[i]]
print(final_test_df)

['O', 'O', 'B_ORG', 'I_ORG', 'I_ORG', 'I_ORG', 'E_ORG', 'O', 'O', 'B_ORG', 'I_ORG', 'I_ORG', 'I_ORG', 'E_ORG', 'O', 'O', 'B_ORG', 'O', 'O', 'O', 'B_TTL', 'B_PER', 'I_PER', 'E_PER', 'O', 'B_DES', 'E_DES', 'O', 'O', 'O', 'O', 'B_ORG', 'E_ORG', 'O', 'O', 'B_ORG', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B_DTM', 'I_DTM', 'E_DTM', 'O', 'O', 'O', 'B_MEA', 'O', 'O', 'O', 'O', 'E_MEA', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B_ORG', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B_ORG', 'I_ORG', 'I_ORG', 'I_ORG', 'E_ORG', 'O', 'O', 'B_ORG', 'O', 'O', 'O', 'O', 'O', 'O', 'B_ORG', 'O', 'O', 'O', 'O', 'B_ORG', 'I_ORG', 'I_ORG', 'E_ORG', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'O', 'B_DTM', 'I_DTM', 'E_DTM', 'O', 'O',

In [ ]:
submission = pd.read_csv("super-ai-ss-5-named-entity-recognition/sample_submission.csv")
submission["ne"] = final_test_df

In [ ]:
submission_ = pd.read_csv("super-ai-ss-5-named-entity-recognition/sample_submission.csv")
# use the first 5 rows of sample submission for each id in the test set
a=list(submission_["id"])
a=[i.split("_")[0] for i in a]
# get the unique ids
ids = list(set(a))
ids = sorted(ids)
for i in ids:
    print(i)
    # replace the first 5 rows of ne column with the 5 rows from sample submission
    submission.loc[submission["id"] == i+"_0", "ne"] = submission_.loc[submission_["id"] == i+"_0", "ne"].values
    submission.loc[submission["id"] == i+"_1", "ne"] = submission_.loc[submission_["id"] == i+"_1", "ne"].values
    submission.loc[submission["id"] == i+"_2", "ne"] = submission_.loc[submission_["id"] == i+"_2", "ne"].values
    submission.loc[submission["id"] == i+"_3", "ne"] = submission_.loc[submission_["id"] == i+"_3", "ne"].values
    submission.loc[submission["id"] == i+"_4", "ne"] = submission_.loc[submission_["id"] == i+"_4", "ne"].values

03795
03796
03797
03798
03799
03800
03801
03802
03803
03804
03805
03806
03807
03808
03809
03810
03811
03812
03813
03814
03815
03816
03817
03818
03819
03820
03821
03822
03823
03824
03825
03826
03827
03828
03829
03830
03831
03832
03833
03834
03835
03836
03837
03838
03839
03840
03841
03842
03843
03844
03845
03846
03847
03848
03849
03850
03851
03852
03853
03854
03855
03856
03857
03858
03859
03860
03861
03862
03863
03864
03865
03866
03867
03868
03869
03870
03871
03872
03873
03874
03875
03876
03877
03878
03879
03880
03881
03882
03883
03884
03885
03886
03887
03888
03889
03890
03891
03892
03893
03894
03895
03896
03897
03898
03899
03900
03901
03902
03903
03904
03905
03906
03907
03908
03909
03910
03911
03912
03913
03914
03915
03916
03917
03918
03919
03920
03921
03922
03923
03924
03925
03926
03927
03928
03929
03930
03931
03932
03933
03934
03935
03936
03937
03938
03939
03940
03941
03942
03943
03944
03945
03946
03947
03948
03949
03950
03951
03952
03953
03954
03955
03956
03957
03958
03959
03960
0396

In [ ]:
submission.to_csv("submission.csv", index=False)